### Content Based Recommendations

In the previous notebook, you were introduced to a way of making recommendations using collaborative filtering.  However, using this technique there are a large number of users who were left without any recommendations at all.  Other users were left with fewer than the ten recommendations that were set up by our function to retrieve....

In order to help these users out, let's try another technique: **content based** recommendations. Let's start off where we were in the previous notebook.

In [70]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from collections import defaultdict
from IPython.display import HTML
#import progressbar
import tests as t
import pickle


%matplotlib inline

# Read in the datasets
movies = pd.read_csv('movies_clean.csv')
reviews = pd.read_csv('reviews_clean.csv')

del movies['Unnamed: 0']
del reviews['Unnamed: 0']


all_recs = pickle.load(open("all_recs.p", "rb"))

In [71]:
movies.head()

movie_id                                              movie  \
0         8      Edison Kinetoscopic Record of a Sneeze (1894)   
1        10                La sortie des usines Lumière (1895)   
2        12                      The Arrival of a Train (1896)   
3        25  The Oxford and Cambridge University Boat Race ...   
4        91                         Le manoir du diable (1896)   

               genre  date  1800's  1900's  2000's  History  News  Horror  \
0  Documentary|Short  1894       1       0       0        0     0       0   
1  Documentary|Short  1895       1       0       0        0     0       0   
2  Documentary|Short  1896       1       0       0        0     0       0   
3                NaN  1895       1       0       0        0     0       0   
4       Short|Horror  1896       1       0       0        0     0       1   

   ...  Fantasy  Romance  Game-Show  Action  Documentary  Animation  Comedy  \
0  ...        0        0          0       0            1          0       0   
1  ...        0        0          0       0            1          0       0   
2  ...        0        0          0       0            1          0       0   
3  ...        0        0          0       0            0          0       0   
4  ...        0        0          0       0            0          0       0   

   Short  Western  Thriller  
0      1        0         0  
1      1        0         0  
2      1        0         0  
3      0        0         0  
4      1        0         0  

[5 rows x 35 columns]

In [72]:
reviews.head()

user_id  movie_id  rating   timestamp                 date  month_1  \
0        1     68646      10  1381620027  2013-10-12 23:20:27        0   
1        1    113277      10  1379466669  2013-09-18 01:11:09        0   
2        2    422720       8  1412178746  2014-10-01 15:52:26        0   
3        2    454876       8  1394818630  2014-03-14 17:37:10        0   
4        2    790636       7  1389963947  2014-01-17 13:05:47        0   

   month_2  month_3  month_4  month_5  ...  month_9  month_10  month_11  \
0        0        0        0        0  ...        0         1         0   
1        0        0        0        0  ...        0         0         0   
2        0        0        0        0  ...        0         1         0   
3        0        0        0        0  ...        0         0         0   
4        0        0        0        0  ...        0         0         0   

   month_12  year_2013  year_2014  year_2015  year_2016  year_2017  year_2018  
0         0          1          0          0          0          0          0  
1         0          1          0          0          0          0          0  
2         0          0          1          0          0          0          0  
3         0          0          1          0          0          0          0  
4         0          0          1          0          0          0          0  

[5 rows x 23 columns]

In [73]:
all_recs

{2: ['Philadelphia (1993)',
  'Training Day (2001)',
  'About Schmidt (2002)',
  'Insomnia (2002)',
  'The United States of Leland (2003)',
  'Shattered Glass (2003)',
  'Man on Fire (2004)',
  'Flipped (2010)',
  'Silver Linings Playbook (2012)',
  'Lawless (2012)',
  '50/50 (2011)',
  'Crazy, Stupid, Love. (2011)',
  'The Perks of Being a Wallflower (2012)',
  'Before I Go to Sleep (2014)',
  'Zero Dark Thirty (2012)',
  'American Hustle (2013)',
  'Django Unchained (2012)',
  'Side Effects (2013)',
  'Gone Girl (2014)',
  'Enough Said (2013)',
  'Nightcrawler (2014)'],
 3: ['Basic Instinct (1992)',
  'The Shawshank Redemption (1994)',
  'The Wedding Ringer (2015)',
  'Life as We Know It (2010)',
  'The Hangover (2009)',
  'Limitless (2011)',
  'The Great Gatsby (2013)',
  'This Is Where I Leave You (2014)',
  'Inception (2010)',
  "The King's Speech (2010)",
  'Love, Rosie (2014)',
  'Now You See Me (2013)',
  'The Intouchables (2011)',
  'Safe Haven (2013)',
  'Before I Go to Sleep

all_recs ### Datasets

From the above, you now have access to three important items that you will be using throughout the rest of this notebook.  

`a.` **movies** - a dataframe of all of the movies in the dataset along with other content related information about the movies (genre and date)


`b.` **reviews** - this was the main dataframe used before for collaborative filtering, as it contains all of the interactions between users and movies.


`c.` **all_recs** - a dictionary where each key is a user, and the value is a list of movie recommendations based on collaborative filtering

For the individuals in **all_recs** who did receive 10 recommendations using collaborative filtering, we don't really need to worry about them.  However, there were a number of individuals in our dataset who did not receive any recommendations.

-----

`1.` Let's start with finding all of the users in our dataset who didn't get all 10 ratings we would have liked them to have using collaborative filtering.  

In [74]:
users_with_all_recs = [] # Store user ids who have all their recommendations in this (10 or more)
users_who_need_recs = []# Store users who still need recommendations here


for k,v in all_recs.items():
    if len(v) >=10:
       
        users_with_all_recs.append(k)
    else:
        users_who_need_recs.append(k)

In [75]:
len(users_who_need_recs)

1325

In [76]:
# A quick test
assert len(users_with_all_recs) == 22187
print("That's right there were still another 31781 users who needed recommendations when we only used collaborative filtering!")

That's right there were still another 31781 users who needed recommendations when we only used collaborative filtering!


### Content Based Recommendations

You will be doing a bit of a mix of content and collaborative filtering to make recommendations for the users this time.  This will allow you to obtain recommendations in many cases where we didn't make recommendations earlier.     

`2.` Before finding recommendations, rank the user's ratings from highest to lowest. You will move through the movies in this order looking for other similar movies.

In [77]:
# create a dataframe similar to reviews, but ranked by rating for each user
df = reviews.sort_values(by='rating',ascending=False)
df

user_id  movie_id  rating   timestamp                 date  month_1  \
0             1     68646      10  1381620027  2013-10-12 23:20:27        0   
499038    37313    387914      10  1497817674  2017-06-18 20:27:54        0   
498972    37297   1877832      10  1401121497  2014-05-26 16:24:57        0   
498974    37298    368226      10  1509161183  2017-10-28 03:26:23        0   
498975    37299   2090488      10  1366687549  2013-04-23 03:25:49        0   
...         ...       ...     ...         ...                  ...      ...   
184769    14241   3450958       0  1508212304  2017-10-17 03:51:44        0   
612049    46079     17136       0  1475412493  2016-10-02 12:48:13        0   
427090    32154   3280262       0  1524752231  2018-04-26 14:17:11        0   
660995    49995     60827       0  1448934523  2015-12-01 01:48:43        0   
524735    39476   1241317       0  1505704222  2017-09-18 03:10:22        0   

        month_2  month_3  month_4  month_5  ...  month_9  month_10  month_11  \
0             0        0        0        0  ...        0         1         0   
499038        0        0        0        0  ...        0         0         0   
498972        0        0        0        0  ...        0         0         0   
498974        0        0        0        0  ...        0         1         0   
498975        0        0        0        0  ...        0         0         0   
...         ...      ...      ...      ...  ...      ...       ...       ...   
184769        0        0        0        0  ...        0         1         0   
612049        0        0        0        0  ...        0         1         0   
427090        0        0        0        0  ...        0         0         0   
660995        0        0        0        0  ...        0         0         0   
524735        0        0        0        0  ...        0         0         0   

        month_12  year_2013  year_2014  year_2015  year_2016  year_2017  \
0              0          1          0          0          0          0   
499038         0          0          0          0          0          1   
498972         0          0          1          0          0          0   
498974         0          0          0          0          0          1   
498975         0          1          0          0          0          0   
...          ...        ...        ...        ...        ...        ...   
184769         0          0          0          0          0          1   
612049         0          0          0          0          1          0   
427090         0          0          0          0          0          0   
660995         1          0          0          1          0          0   
524735         0          0          0          0          0          1   

        year_2018  
0               0  
499038          0  
498972          0  
498974          0  
498975          0  
...           ...  
184769          0  
612049          0  
427090          1  
660995          0  
524735          0  

[712337 rows x 23 columns]

### Similarities

We have talked in our first Lecture at ITI about similarity metrics and the difference between dot product vs. cosine similarity vs euclidean distance. Here we will apply what we have learnt. 


In many cases, it turns out that one of the fastest ways we can find out how similar items are to one another (when our matrix isn't totally sparse like it was in the earlier section) is by simply using matrix multiplication.

For us to pull out a matrix that describes the movies in our dataframe in terms of content, we might just use the indicator variables related to **year** and **genre** for our movies.  

Then we can obtain a matrix of how similar movies are to one another by taking the dot product of this matrix with itself.  

We can perform the dot product on a matrix of movies with content characteristics to provide a movie by movie matrix where each cell is an indication of how similar two movies are to one another.  




`3.` Create a numpy array that is a matrix of indicator variables related to year (by century) and movie genres by movie.  Perform the dot product of this matrix with itself (transposed) to obtain a similarity matrix of each movie with every other movie.  The final matrix should be 31245 x 31245.

In [78]:
# Subset so movie_content is only using the dummy variables for each genre and the 3 century based year dummy columns

movie_content = np.array(movies.iloc[:1000,4:])
# Take the dot product to obtain a movie x movie matrix of similarities
dot_prod_movies = np.dot(movie_content,movie_content.T)
dot_prod_movies.shape

(1000, 1000)

In [79]:
movies.head()

movie_id                                              movie  \
0         8      Edison Kinetoscopic Record of a Sneeze (1894)   
1        10                La sortie des usines Lumière (1895)   
2        12                      The Arrival of a Train (1896)   
3        25  The Oxford and Cambridge University Boat Race ...   
4        91                         Le manoir du diable (1896)   

               genre  date  1800's  1900's  2000's  History  News  Horror  \
0  Documentary|Short  1894       1       0       0        0     0       0   
1  Documentary|Short  1895       1       0       0        0     0       0   
2  Documentary|Short  1896       1       0       0        0     0       0   
3                NaN  1895       1       0       0        0     0       0   
4       Short|Horror  1896       1       0       0        0     0       1   

   ...  Fantasy  Romance  Game-Show  Action  Documentary  Animation  Comedy  \
0  ...        0        0          0       0            1          0       0   
1  ...        0        0          0       0            1          0       0   
2  ...        0        0          0       0            1          0       0   
3  ...        0        0          0       0            0          0       0   
4  ...        0        0          0       0            0          0       0   

   Short  Western  Thriller  
0      1        0         0  
1      1        0         0  
2      1        0         0  
3      0        0         0  
4      1        0         0  

[5 rows x 35 columns]

In [80]:
# create checks for the dot product matrix
assert dot_prod_movies.shape[0] == 1000
assert dot_prod_movies.shape[1] == 1000
assert dot_prod_movies[0, 0] == np.max(dot_prod_movies[0])
print("Looks like you passed all of the tests.  Though they weren't very robust - if you want to write some of your own, I won't complain!")

Looks like you passed all of the tests.  Though they weren't very robust - if you want to write some of your own, I won't complain!


### For Each User...


Now you have a matrix where each user has their ratings ordered.  You also have a second matrix where movies are each axis, and the matrix entries are larger where the two movies are more similar and smaller where the two movies are dissimilar.  This matrix is a measure of content similarity. Therefore, it is time to get to the fun part.

For each user, we will perform the following:

    i. For each movie, find the movies that are most similar that the user hasn't seen.

    ii. Continue through the available, rated movies until 10 recommendations or until there are no additional movies.

As a final note, you may need to adjust the criteria for 'most similar' to obtain 10 recommendations.  As a first pass, I used only movies with the highest possible similarity to one another as similar enough to add as a recommendation.

`3.` In the cell below, complete each of the functions needed for making content based recommendations.

In [81]:
index = np.where(movies.movie_id == 10 )[0][0]

In [82]:
np.max(dot_prod_movies[np.where(movies.movie_id == 10 )[0][0]])

3

In [83]:
np.fill_diagonal(dot_prod_movies,0)

In [84]:
dot_prod_movies

array([[0, 3, 3, ..., 0, 0, 0],
       [3, 0, 3, ..., 0, 0, 0],
       [3, 3, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 1, 1],
       [0, 0, 0, ..., 1, 0, 2],
       [0, 0, 0, ..., 1, 2, 0]])

In [85]:
arr = np.where(dot_prod_movies[index]==np.max(dot_prod_movies[index]))[0]
arr

array([0, 2])

In [86]:
movies[movies.index.isin(arr)]['movie']

0    Edison Kinetoscopic Record of a Sneeze (1894)
2                    The Arrival of a Train (1896)
Name: movie, dtype: object

In [87]:
movie_lst = list(movies[movies.index.isin([0,2])]['movie'])
movie_lst

['Edison Kinetoscopic Record of a Sneeze (1894)',
 'The Arrival of a Train (1896)']

In [88]:
lst=list(df[df.user_id==1]['movie_id'])
lst

[68646, 113277]

In [89]:
def f7(seq):
    seen = set()
    seen_add = seen.add
    return [x for x in seq if not (x in seen or seen_add(x))]




f7(list(df[~df.movie_id.isin(lst)]['movie_id'][:10]))

[387914,
 1877832,
 368226,
 2090488,
 1649419,
 1675434,
 2278871,
 2338151,
 2267998,
 1937118]

In [90]:
def find_similar_movies(movie_id):
    '''
    INPUT
    movie_id - a movie_id 
    OUTPUT
    similar_movies - an array of the most similar movies by title
    '''
    # find the row of each movie id
    index = np.where(movies.movie_id == movie_id )[0][0]
    
    # find the most similar movie indices - to start I said they need to be the same for all content
    np.fill_diagonal(dot_prod_movies,0)
    arr=np.where(dot_prod_movies[index]==np.max(dot_prod_movies[index]))[0]
    
    # pull the movie titles based on the indices
    similar_movies = movies[movies.index.isin(arr)]['movie']
    
    return similar_movies
    

def get_movie_names(movie_ids):
    '''
    INPUT
    movie_ids - a list of movie_ids
    OUTPUT
    movies - a list of movie names associated with the movie_ids
    
    '''
    # return a list with movie names for the list of input movie IDs
    movie_lst = list(movies[movies.index.isin(movie_ids)]['movie'])
    return movie_lst


def make_recs():
    '''
    INPUT
    None
    OUTPUT
    recs - a dictionary with keys of the user and values of the recommendations
    '''
    # Create dictionary to return with users and ratings
    
    recs = dict()
    #df
    # For each user
        

        # Pull only the reviews the user has seen

        # Look at each of the movies (highest ranked first), 
        # pull the movies the user hasn't seen that are most similar
        # These will be the recommendations - continue until 10 recs 
        # or you have depleted the movie list for the user

    for i in users_who_need_recs:
            watched =list(df[df.user_id==i]['movie_id'])
            
            if i not in  recs:
                recs[i]=[]
           
            recs[i]= f7(list(df[~df.movie_id.isin(watched)]['movie_id'][:10]))

    return recs

In [91]:
recs = make_recs()

### How Did We Do?

Now that you have made the recommendations, how did we do in providing everyone with a set of recommendations?

`4.` Use the cells below to see how many individuals you were able to make recommendations for, as well as explore characteristics about individuals for whom you were not able to make recommendations.  

In [92]:
# Explore recommendations
users_without_all_rec = []#store user ids without recs
users_with_all_rec = [] # users with all recs here
no_rec = []# users with no recommendations

for k,v in recs.items():
    if len(v) >=10:
       
        users_with_all_rec.append(k)
    elif len(v)>0:
        users_without_all_rec.append(k)
    else:
        no_rec.append(k)

In [93]:
# Some characteristics of my content based recommendations
users_without_all_recs = users_without_all_rec#store user ids without recs
users_with_all_recs = users_with_all_rec # users with all recs here
no_recs = no_rec # users with no recommendations

print("There were {} users without all 10 recommendations we would have liked to have.".format(len(users_without_all_recs)))
print("There were {} users with all 10 recommendations we would like them to have.".format(len(users_with_all_recs)))
print("There were {} users with no recommendations at all!".format(len(no_recs)))

There were 0 users without all 10 recommendations we would have liked to have.
There were 1325 users with all 10 recommendations we would like them to have.
There were 0 users with no recommendations at all!
